In [7]:
%reload_ext autoreload
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


[autoreload of models failed: Traceback (most recent call last):
  File "/home/xandao/miniconda3/lib/python3.9/site-packages/IPython/extensions/autoreload.py", line 261, in check
    superreload(m, reload, self.old_objects)
  File "/home/xandao/miniconda3/lib/python3.9/site-packages/IPython/extensions/autoreload.py", line 484, in superreload
    update_generic(old_obj, new_obj)
  File "/home/xandao/miniconda3/lib/python3.9/site-packages/IPython/extensions/autoreload.py", line 381, in update_generic
    update(a, b)
  File "/home/xandao/miniconda3/lib/python3.9/site-packages/IPython/extensions/autoreload.py", line 319, in update_class
    if (old_obj == new_obj) is True:
  File "/home/xandao/miniconda3/lib/python3.9/site-packages/sqlalchemy/sql/operators.py", line 523, in __eq__
    return self.operate(eq, other)
  File "/home/xandao/miniconda3/lib/python3.9/site-packages/sqlalchemy/orm/attributes.py", line 444, in operate
    return op(self.comparator, *other, **kwargs)  # type: ignore

In [8]:
import os
import pathlib
import sys

sys.path.append(os.path.dirname(os.path.dirname(os.path.abspath('main.ipynb'))))

import database as db
from models import DataTrustedIdentifier, Image, create_info_image
from sqlalchemy import and_
from sqlalchemy.orm import Session

## Database connection

In [9]:
session: Session
engine, session = db.connect()
engine.echo=False

2023-03-27 15:15:39,639 INFO sqlalchemy.engine.Engine select pg_catalog.version()
2023-03-27 15:15:39,640 INFO sqlalchemy.engine.Engine [raw sql] {}
2023-03-27 15:15:39,641 INFO sqlalchemy.engine.Engine select current_schema()
2023-03-27 15:15:39,641 INFO sqlalchemy.engine.Engine [raw sql] {}
2023-03-27 15:15:39,642 INFO sqlalchemy.engine.Engine show standard_conforming_strings
2023-03-27 15:15:39,642 INFO sqlalchemy.engine.Engine [raw sql] {}


## Create table info_image and fill table

In [10]:
db.create_table(engine, Image)

In [11]:
def fill_table_info_image(color_mode, image_size, result, seq):
    for path in result:
        record_exist = session.query(Image) \
            .filter(and_(Image.color_mode.__eq__(color_mode),
                         Image.height.__eq__(image_size[0]),
                         Image.width.__eq__(image_size[1]),
                         Image.path.__eq__(path),
                         Image.seq_id.__eq__(seq))) \
            .all()
        if len(record_exist) == 0:
            print('inserted new record')
            image = create_info_image(color_mode, path, seq, image_size[0], image_size[1])
            session.add(image)
            session.commit()


def set_path_image(color_mode, image_size, list_images, query):
    for i, q in enumerate(query):
        result = sorted([str(image) for image in list_images if q.barcode in str(image.stem) and os.path.exists(image)])
        print('founded %d files' % len(result))
        if len(result) > 0:
            fill_table_info_image(color_mode, image_size, result, q.seq)

In [12]:
for color in ['rgb', 'grayscale']:
    for image_size in ['256', '400', '512']:
        column_name = 'path_%s_%s' % (image_size, color)
        path_fotos = '/media/xandao/c2f58d30-ff2c-47f7-95af-91ad6fd69760/dataset/dataset-52k-sp-RGB-resize-xcf-mask-segmented/RGB/%s/w_pred_mask' % (image_size)
        list_images = [image for image in pathlib.Path(path_fotos).rglob('*.jpeg') if image.is_file()]
        columns = [DataTrustedIdentifier.barcode, DataTrustedIdentifier.seq]
        query = session.query(*columns).all()
        if len(list_images) > 0 and len(query) >= 0:
            set_path_image(color, (int(image_size), int(image_size)), list_images, query)

founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 0 files
founded 1 files
inserted new record
founded 3 files
inserted new record
inserted new record
inserted new record
founded 1 files
inserted new record
founded 2 files
inserted new record
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 2 files
inserted new record
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
founded 1 files
inserted new record
foun

## Close connection

In [14]:
session.close()
engine.dispose()